In [ ]:
!pip install pandasql
!pip install numpy_financial

In [ ]:
import numpy as np
import pandas as pd
import pandasql as ps
import numpy_financial as npf

In [ ]:
df = pd.DataFrame(dict(index=['demand','price','sales','cost','expenses','cash'],year1=[0,10,0,0,0,0],year2=[0,10,0,0,0,0],year3=[0,10,0,0,0,0],year4=[0,10,0,0,0,0]))

In [ ]:
df.set_index('index',inplace=True)

In [ ]:
df

year1  year2  year3  year4
index                               
demand        0      0      0      0
price        10     10     10     10
sales         0      0      0      0
cost          0      0      0      0
expenses      0      0      0      0
cash          0      0      0      0

In [ ]:
# not relevent
# calculate all at once
# import numpy as np
# import pandas as pd

# class make_fr():

#   def __init__(self,Number_of_Periods,Number_of_Simulations):
#     self.pd = Number_of_Periods
#     self.Number_of_Simulations = Number_of_Simulationscas
#     return(None)

#   def NDist(self,**details):
#     """
#     Provide variable name , mean & std
#     e.g.:
#       demand = [50,5]
#       temp = [20,2]

#     """
#     ND = {}

#     for d in details:
#       col = [np.random.normal(details[d][0],details[d][1],self.pd) for i in range(self.Number_of_Simulations)]
#       ND.update({d:col})

#     return(ND)

In [ ]:

# one by one
import numpy as np
import pandas as pd
import pandasql as ps

class make_fr():

  def __init__(self,data,number_of_simulations,feature_to_simulate,sql_query,calculate_NPV_IRR=False,Required_Rate=None,Initial_investment=None):
    self.data = data.transpose()
    self.pd = data.shape[1]
    self.number_of_simulations = number_of_simulations
    self.query = sql_query
    self.feature_to_simulate = feature_to_simulate
    self.all_random_numbers = {}
    self.calculate_NPV_IRR = calculate_NPV_IRR
    self.Required_Rate = Required_Rate

    if Initial_investment < 0:
      self.Initial_investment = Initial_investment
    else:
      self.Initial_investment = Initial_investment * -1.0

    return(None)

  # normal dist
  def NDist(self,**details):
    """
    Provide variable name , mean & std
    e.g.:
      demand = [50,5]
      temperature = [20,2]

    """
    self.n_details = details
    self.ND = {}

    for d in details:
      col = np.random.normal(details[d][0],details[d][1],(self.number_of_simulations,self.pd)) # self.pd is numbers of years (columns)
      self.ND.update({d:col})

    # update the global dict
    self.all_random_numbers.update(self.ND)
    return(self.ND)


  #triangle distribution
  def TriDist(self,**details):
    """
    Provide variable name , lowest value, most likely value & maximum value
    e.g.:
      demand = [10,100,250]
      temp = [-10,18,40]

    """
    self.t_details = details
    self.TD = {}
    for d in details:
      col = np.random.triangular(details[d][0],details[d][1],details[d][2],(self.number_of_simulations,self.pd))
      self.TD.update({d:col})
    
    # update the global dict
    self.all_random_numbers.update(self.TD)
    return(self.TD)


  def simul8(self):

    copy_data = self.data.copy()
 
    self.full_data = []
    self.feature_only_sum = []
    self.NPV = []
    self.IRR =[]

   
    for i in range(self.number_of_simulations):

      # get the random number for the current i
      for k,v in zip(fr.all_random_numbers.keys(),fr.all_random_numbers.values()):
        #print(k,v[i])
        copy_data[k] = v[i]
        copy_data_updated = copy_data.copy()

      # once we have all the random numbers in place, we need to apply the sql formulas
      data_index  = self.data.index
      df = copy_data_updated.reset_index(drop=True)
      df_refreshed = ps.sqldf(self.query,locals())

      # now check if we need to calculate NPV/IRR or a simple sum 
      if (self.Required_Rate is not None) & (self.calculate_NPV_IRR == True) & (self.Initial_investment is not None):
        # add initial investment to the cash
        c = list(df_refreshed[self.feature_to_simulate])
        c.insert(0,self.Initial_investment)

        #calculate npv
        npv = npf.npv(self.Required_Rate,c)
        self.NPV.append(npv)

        #calculate irr
        irr = npf.mirr(c,self.Required_Rate,self.Required_Rate)
        self.IRR.append(irr)
      
      # now calculate the sum of all the cash
      if self.Initial_investment is None:
        cash = np.sum(df_refreshed[self.feature_to_simulate])
      else:
        cash = self.Initial_investment + np.sum(df_refreshed[self.feature_to_simulate])
      # add to list
      self.feature_only_sum.append(cash)

      # now save the full data frame
      self.full_data.append(df_refreshed)


    return(self.full_data)







In [ ]:
q = "select demand,price,demand*price as sales, cost ,demand*cost as expenses, (demand*price)-(demand*cost) as cash from df"

In [ ]:
fr = make_fr(data=df,
             number_of_simulations= 10000,
             feature_to_simulate= 'cash',
             sql_query= q,
             calculate_NPV_IRR= True,
             Required_Rate= 0.20,
             Initial_investment= -500)

In [ ]:

## Shouldn't the fn calls be inside simulate.
fr.NDist(price=[10,2])

{'price': array([[11.9800089 ,  9.75711631, 12.31115621, 10.57209232],
        [10.67568898, 11.58335789, 11.50739421, 13.49458946],
        [ 7.43663947,  9.25810758,  8.77896799,  9.08537569],
        ...,
        [10.23943645,  8.84101106,  8.58517913,  7.15647669],
        [13.40102018, 10.80740097,  9.8176898 , 10.62372308],
        [ 8.32120089,  7.51441497, 14.61500243, 11.7119403 ]])}

In [ ]:
fr.TriDist(cost=[2,8,12],demand=[10,100,250])

{'cost': array([[11.02907932,  9.57834522,  3.65990389,  7.13351981],
        [ 7.12085625,  6.08059559,  6.50974621, 10.10573565],
        [ 8.6972503 ,  2.42920034,  7.86222801,  7.91613785],
        ...,
        [10.1409436 , 10.12049894,  4.58857105,  9.95169883],
        [ 9.81746457,  7.95988741, 10.53667143,  9.62556687],
        [ 5.32302886,  8.52084269,  8.20445011,  6.01440056]]),
 'demand': array([[ 78.92480852,  57.3397361 , 111.94755758, 108.71243342],
        [129.40554466, 119.01136825, 165.52615368,  38.96003321],
        [227.44063355, 109.97975746, 235.43718725, 112.668603  ],
        ...,
        [ 98.37055149, 181.77796552,  60.80981842,  23.74481183],
        [ 94.41483739,  89.67792308,  95.95018129, 156.52450838],
        [ 85.1905293 , 119.55409457, 183.63112   ,  99.22954281]])}

In [ ]:
fr.Initial_investment

-500

In [ ]:
 %%time
 l = fr.simul8()

CPU times: user 1min 11s, sys: 184 ms, total: 1min 11s
Wall time: 1min 11s


In [ ]:
fr.full_data[3]

demand      price        sales       cost     expenses        cash
0   56.270484   8.333791   468.946433   8.053659   453.183285   15.763148
1   65.263166   9.298614   606.857021  10.441096   681.419002  -74.561981
2  200.721058   9.125065  1831.592746   7.678961  1541.329154  290.263591
3  130.115154  11.314647  1472.207031   9.302159  1210.351872  261.855159

In [ ]:
fr.feature_only_sum[:10]

[927.6047759672356,
 1574.1776438802522,
 311.8985111046518,
 -6.680082945502022,
 317.89610890130166,
 -82.76480617990819,
 541.378231750713,
 1129.232866602401,
 1464.317961764968,
 1680.2265934482684]

In [ ]:
fr.NPV[3]

-244.38612302300717

In [ ]:
fr.IRR[3]*100

3.6724657781203485

In [ ]:
c = list(fr.full_data[3]['cash'])

In [ ]:
c.insert(0,-500)

In [ ]:
len(fr.ND['price'])

10000

In [ ]:
df = pd.DataFrame(fr.IRR)
index = df[0].index[df[0].apply(np.isnan)]
index = list(map(int, index))
index

df = pd.concat([pd.DataFrame(fr.full_data[i]) for i in index],
          ignore_index=True)
df

demand      price        sales       cost     expenses        cash
0   178.197382   6.313694  1125.083725   8.728936  1555.473540 -430.389814
1    25.910155   9.318357   241.440078   9.634399   249.628767   -8.188690
2   215.782873   6.579903  1419.830396   7.126596  1537.797329 -117.966933
3    92.332789   9.847247   909.223781  10.997216  1015.403612 -106.179831
4   144.549567   8.072578  1166.887661   8.971216  1296.785426 -129.897765
5   124.453314   8.406412  1046.205778   9.197645  1144.677351  -98.471573
6   208.775610  10.095265  2107.645064  10.683173  2230.385982 -122.740919
7   176.107964   5.327061   938.137918   8.579811  1510.973080 -572.835162
8    59.889948   6.926993   414.857276   7.818974   468.277920  -53.420644
9   142.399745   6.651651   947.193464   7.104902  1011.736301  -64.542837
10   90.493960   5.715730   517.239006   9.900141   895.902935 -378.663930
11   60.775561  10.144605   616.544074  11.175474   679.195718  -62.651644
12  114.824573   7.200983   826.849824   8.073759   927.065983 -100.216159
13   88.493193   6.691858   592.183924   8.972273   793.985087 -201.801163
14   85.529896   7.628424   652.458305   8.092560   692.155800  -39.697495
15   34.353704   5.997185   206.025526   8.147846   279.908682  -73.883157
16   65.513843   3.905979   255.895673   8.433783   552.529554 -296.633881
17  174.537995   8.129766  1418.952992  10.108191  1764.263360 -345.310368
18   64.660247   8.537348   552.027014   8.925045   577.095640  -25.068627
19  163.866127   5.528949   906.007408  10.625406  1741.144100 -835.136692
20  101.902071   7.464671   760.665400   7.850146   799.946163  -39.280763
21  126.474878   8.059562  1019.332123  10.956119  1385.673811 -366.341688
22   81.679192   7.451764   608.654035   8.172118   667.492028  -58.837992
23  116.850969   8.176357   955.415224   8.860580  1035.367352  -79.952128
24   42.077258   7.782649   327.472530   8.218685   345.819707  -18.347177
25   94.557554  10.127567   957.637997  10.962244  1036.562998  -78.925001
26   85.472084   9.442173   807.042192  10.113440   864.416793  -57.374600
27   66.469820   6.434575   427.705049   9.618821   639.361285 -211.656236
28  134.479923   8.510946  1144.551352  10.316347  1387.341536 -242.790185
29   71.284343   5.777057   411.813697   6.478230   461.796350  -49.982653
30  201.183092  10.722771  2157.240153  11.379698  2289.402827 -132.162675
31  134.812155   7.708295  1039.171811   9.760995  1315.900789 -276.728978
32  191.681263   6.888004  1320.301254   8.057706  1544.511278 -224.210024
33  151.203796   6.881445  1040.500557   9.723001  1470.154670 -429.654113
34  100.363677   5.764104   578.506701   7.846225   787.476012 -208.969310
35  141.070867   6.494178   916.139264   8.954511  1263.220628 -347.081365
36   99.585649   8.239201   820.506183   8.490847   845.566543  -25.060360
37  158.699013   8.587758  1362.868725  10.045378  1594.191647 -231.322921
38   89.736255   7.163612   642.835681   9.814821   880.745311 -237.909630
39   62.836222   7.835812   492.372816   8.455061   531.284065  -38.911249
40  163.217883   6.112664   997.696148   9.161212  1495.273592 -497.577444
41  209.207522   9.576258  2003.425277   9.881931  2067.374231  -63.948953
42  104.966999   9.381426   984.740119  11.067027  1161.672607 -176.932487
43   98.058704   9.262289   908.248069   9.354453   917.285552   -9.037483
44  231.903039   7.879646  1827.313798   7.938956  1841.067958  -13.754160
45   91.316235   6.381493   582.733896  10.705723   977.606280 -394.872384
46  165.082005   5.814366   959.847276   6.230173  1028.489408  -68.642132
47   74.579436   8.772817   654.271733  10.037152   748.565103  -94.293371
48  122.759614  10.651983  1307.633285  10.792337  1324.863184  -17.229900
49  152.647291   7.723425  1178.959873   8.500348  1297.555070 -118.595197
50  225.887585   9.202079  2078.635288  10.211323  2306.611037 -227.975749
51   74.019382   8.312873   615.313748  11.185740   827.961544 -212.647797
52   75.670420   7.427883   562.0

In [ ]:
c

[-500,
 15.763148001032164,
 -74.56198124941398,
 290.2635912499252,
 261.8551590529546]

In [ ]:
npf.npv(.20,c)

-244.38612302300717

In [ ]:
(npf.irr(c)) *100

-0.371040311969284

In [ ]:
np.min([i for i in fr.IRR if i is not np.nan])

-0.7128559337194914

In [ ]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'colab'
fig = px.histogram( pd.DataFrame(fr.feature_only_sum,columns=['cash']), x="cash",histnorm='probability')
fig.show()

In [ ]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'colab'
fig = px.histogram( pd.DataFrame(fr.feature_only_sum,columns=['cash']), x="cash",histnorm='probability',cumulative=True)
fig.show()

In [ ]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'colab'
fig = px.histogram( pd.DataFrame(stats.zscore(fr.feature_only_sum),columns=['cash']), x="cash")
fig.show()

In [ ]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'colab'
fig = px.histogram( pd.DataFrame(fr.IRR,columns=['cash']), x="cash",histnorm='probability')
fig.show()

In [ ]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'colab'
fig = px.histogram( pd.DataFrame(fr.NPV,columns=['NPV']), x="NPV")
fig.show()

In [ ]:
pd.DataFrame(fr.feature_only_sum,columns=['cash'])

cash
0      927.604776
1     1574.177644
2      311.898511
3       -6.680083
4      317.896109
...           ...
9995   462.695156
9996  1048.849568
9997  -546.232920
9998   180.949414
9999  1377.634473

[10000 rows x 1 columns]

In [ ]:
np.average(fr.IRR)

nan

In [ ]:
from scipy import stats

In [ ]:
#stats.zscore()
data = []


In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Histogram(name='Cash count', x= fr.feature_only_sum),
    secondary_y=False,
)
fig.add_trace(
    go.Histogram(name = 'Cumulative probability of Cash', x = fr.feature_only_sum,histnorm='probability',
                 cumulative={'enabled':True, 'direction': 'increasing','currentbin':'include'}, opacity= 0.5,
                 hoverlabel = dict(namelength = -1)),
                 secondary_y=True,)

fig.update_layout(
    title_text="Distribution of cash values",
    title_x=0.43
)

# Set x-axis title
fig.update_xaxes(title_text="Cash values")

# Set y-axes titles
fig.update_yaxes(title_text="<b>Count of cash values </b>", secondary_y=False)
fig.update_yaxes(title_text= "<b>Cumulative probability of cash values</b>", secondary_y=True)
fig.show()


In [ ]:
import plotly.graph_objs as go
#import plotly.offline as py
import plotly.io as pio
import pandas as pd
import numpy as np
from ipywidgets import interactive, HBox, VBox

pio.renderers.default = 'colab'
py.init_notebook_mode()

f = go.FigureWidget([go.Histogram(name='Cash count', x= fr.feature_only_sum),
    secondary_y=False,), go.Histogram(name = 'Cumulative probability of Cash', x = fr.feature_only_sum,histnorm='probability',
                 cumulative={'enabled':True, 'direction': 'increasing','currentbin':'include'}, opacity= 0.5,
                 hoverlabel = dict(namelength = -1)),
                 secondary_y=True,)
])
scatter = f.data[0]
N = len(df)

def update_axes(xaxis, yaxis):
    scatter = f.data[0]
    scatter.x = df[xaxis]
    scatter.y = df[yaxis]
    with f.batch_update():
        f.layout.xaxis.title = xaxis
        f.layout.yaxis.title = yaxis
        scatter.x = scatter.x + np.random.rand(N)/10 *(df[xaxis].max() - df[xaxis].min())
        scatter.y = scatter.y + np.random.rand(N)/10 *(df[yaxis].max() - df[yaxis].min())

axis_dropdowns = interactive(update_axes, yaxis = df.select_dtypes('int64').columns, xaxis = df.select_dtypes('int64').columns)

# Create a table FigureWidget that updates on selection from points in the scatter plot of f
t = go.FigureWidget([go.Table(
    header=dict(values=['ID','Classification','Driveline','Hybrid'],
                fill = dict(color='#C2D4FF'),
                align = ['left'] * 5),
    cells=dict(values=[df[col] for col in ['ID','Classification','Driveline','Hybrid']],
               fill = dict(color='#F5F8FF'),
               align = ['left'] * 5))])

def selection_fn(trace,points,selector):
    t.data[0].cells.values = [df.loc[points.point_inds][col] for col in ['ID','Classification','Driveline','Hybrid']]

scatter.on_selection(selection_fn)
import plotly.io as pio
pio.renderers.default = 'colab'
# Put everything together
VBox((HBox(axis_dropdowns.children),f,t))